In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import Span
from shapely.geometry import Point
import geopandas as gpd
import glob
import bokeh
from datetime import datetime
from bokeh.layouts import column
from bokeh.models import Legend, Tabs, TabPanel
from bokeh.core.validation.warnings import MISSING_RENDERERS, EMPTY_LAYOUT

# Set fonts for matplotlib
plt.rcParams["font.family"] = "Arial"
plt.rcParams["font.size"] = 14

In [2]:

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(EMPTY_LAYOUT, True)

{Warning(code=1002, name='EMPTY_LAYOUT', description='Layout has no children')}

In [3]:
# Function to convert a pandas dataframe to a geopandas dataframe
def convert_to_gdf(df):
    geometry = [Point(xy) for xy in zip(df.longitude, df.latitude)]
    gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry=geometry)

    return gdf

# Bangladesh - Flooding and Cyclone

For this analysis, two datasets are utilized:

**1. Cyclone Remal Business Activity Trends Dataset**

The dataset triggered by Cyclone Remal contains daily data from **May 27th, 2024 to June 10th, 2024**

The baseline date for this dataset is **April 12, 2024** (45 days before the crisis).

**2. Flood-Triggered Business Activity Trends Dataset**

The Flood-Triggered Business Activity Trends dataset contains daily data from **August 25th, 2024 - September 5th, 2024**.  

The baseline date for this dataset is **July 11th, 2024** (45 days before the crisis).

## Purpose of this Notebook:
This notebook demonstrates the following analyses:
- **Visualizing Business Activity Data by Vertical for the National Population:**  
  Examining how different business sectors (verticals) have been impacted during and after the crisis.  
- **Analyzing Changes in Business Activity by Region and Vertical:**  
  Visualizing how trends vary across administrative regions (Admin 2) and specific business sectors.  

In [4]:
# Read shapefiles from HdX UNOCHA
bgd_adm2 = gpd.read_file(
    "../../data/bgd_adm_bbs_20201113_SHP/bgd_admbnda_adm2_bbs_20201113.shp"
)
bgd_adm1 = gpd.read_file(
    "../../data/bgd_adm_bbs_20201113_SHP/bgd_admbnda_adm1_bbs_20201113.shp"
)

c:\Users\wb614536\.conda\envs\env_bgd\Lib\site-packages\pyogrio\core.py:35: RuntimeWarning: Could not detect GDAL data files.  Set GDAL_DATA environment variable to the correct path.
  _init_gdal_data()


### Data Information Summary

This dataset provides insights into business activity at the [GADM 2](https://gadm.org/) level, covering 64 districts in Bangladesh. 

#### **Activity Quantile (activity_quantile):**
The activity quantile metric is used to measure changes in Business Activity.

- **Purpose:** Measures changes in business activity relative to a baseline period.  
- **Key Values:**
  - **0.5:** Normal activity (baseline level).  
  - **Above 0.5:** Increased activity.  
  - **Below 0.5:** Decreased activity.  

#### **Calculation Overview:**
1. Compare daily activity of business pages to their baseline activity levels (quantiles).  
2. Aggregate and standardize these values to follow a normal distribution.  
3. Apply a cumulative probability transformation to derive a value between **0 and 1**.  
4. Average results over 7 days to reduce daily noise.  
5. Provides equal weight to all businesses, avoiding bias from more active pages. 


In [5]:
# Read the business activity data

# flood related 
businessActivity2024_flood = pd.read_csv("../../data/business-activity-trends/raw/business-activity-trends-flooding-bangladesh-1587776021952166-20240825-20240905(in).csv")
businessActivity2024_flood['country'] = "BD"
businessActivity2024_flood = businessActivity2024_flood[businessActivity2024_flood["country"] == "BD"]


In [6]:
businessActivity2024_extra = pd.read_csv("../../data/business-activity-trends/raw/bangladesh-india-sri_lanka-business-activity-trends-crisis-20240509-20241216.csv")
# filter country == BGD
businessActivity2024_extra = businessActivity2024_extra[businessActivity2024_extra["country"] == "BGD"]
# change country BGD to BD
businessActivity2024_extra['country'] = "BD"


In [7]:
# Convert columns to datetime

businessActivity2024_flood["ds"] = businessActivity2024_flood["ds"].apply(
    lambda x: pd.to_datetime(x)
)

businessActivity2024_extra["ds"] = businessActivity2024_extra["ds"].apply(
    lambda x: pd.to_datetime(x)
)

# filter data for cyclone date May 27th to June 10h 2024
businessActivity2024_extra = businessActivity2024_extra[(businessActivity2024_extra['ds'] >= '2024-05-27') & (businessActivity2024_extra['ds'] <= '2024-06-10')]

In [8]:
# Get the unique business verticals 
business_verticals = list(businessActivity2024_flood["business_vertical"].unique())

print(
    f"Bangladesh Political Crisis Business Actvity Trends has the following business verticals {business_verticals}"
)

Bangladesh Political Crisis Business Actvity Trends has the following business verticals ['Grocery & Convenience Stores', 'Retail', 'All', 'Home Services', 'Professional Services', 'Lifestyle Services', 'Travel', 'Public Good', 'Local Events', nan, 'Manufacturing', 'Restaurants', 'Business & Utility Services']


In [9]:
# read flood related data

import geopandas as gpd

flood_fgb_path = "../../data/flood/raw/eastbgd_floods_202408_20241024155022.pmtiles.flooded_area.fgb"
flooded_gdf = gpd.read_file(flood_fgb_path)

# read csv remal
# data downloaded from: UNOSTAT : https://unosat-rm.cern.ch/FloodAI/apps/BGD/?activation=AI20240502BGD
remal_flood = pd.read_csv("../../data/flood/raw/PopulationExposed_2024-05-24_TO_2024-05-29.csv")
# read csv flood
august_flood = pd.read_csv("../../data/flood/raw/PopulationExposed_2024-08-23_TO_2024-08-29.csv")

# compute flood percentage in both datasets

# Calculate the Flood Percentage
remal_flood["Flood_Percentage"] = (remal_flood["Flooded_Area_SqKM"] / remal_flood["Observed_Area_SqKM"]) * 100

# Standardize the Admin2 column for merging (strip spaces and convert to uppercase)
remal_flood["Admin2"] = remal_flood["Admin2"].str.strip().str.upper()

august_flood["Flood_Percentage"] = (august_flood["Flooded_Area_SqKM"] / august_flood["Observed_Area_SqKM"]) * 100

# Standardize the Admin2 column for merging (strip spaces and convert to uppercase)
august_flood["Admin2"] = august_flood["Admin2"].str.strip().str.upper()






In [10]:
from bokeh.models import Div, Span, Label
from bokeh.layouts import column

def get_line_plot(
    businessActivity,
    title,
    source,
    subtitle=None,
    vertical_dates=None,
    vertical_labels=None,
    limitations_note=None,  # Add note parameter
    label_offset=10  # Offset for labels to the right
):
    # Create the main figure
    p2 = figure(
        x_axis_type="datetime", 
        width=1000, 
        height=600, 
        toolbar_location="above",
        sizing_mode="stretch_width"  
    )
    p2.add_layout(Legend(), "right")

    # Define a color palette 
    from bokeh.palettes import Category20
    color_palette = Category20[15]  

    # Plot lines for each business vertical
    for id, business_vertical in enumerate(businessActivity["business_vertical"].unique()):
        if pd.isnull(business_vertical):  # Handle missing values in business_vertical
            business_vertical = "Unknown"

        business_vertical = str(business_vertical)  # Ensure it's a string

        df = businessActivity[businessActivity["business_vertical"] == business_vertical][
            ["ds", "activity_quantile"]
        ].reset_index(drop=True)

        p2.line(
            df["ds"],
            df["activity_quantile"],
            line_width=2,
            line_color=color_palette[id % len(color_palette)],  # Handle color overflow
            legend_label=business_vertical,
        )

    # Configure legend
    p2.legend.click_policy = "hide"
    p2.legend.label_text_font_size = "10pt"

    # Horizontal line at 0.5
    baseline = Span(
        location=0.5, 
        dimension="width", 
        line_color="black", 
        line_dash="dashed", 
        line_width=2
    )
    p2.add_layout(baseline)

    # Add vertical lines and labels if provided
    if vertical_dates and vertical_labels:
        for date, label_text in zip(vertical_dates, vertical_labels):
            vline = Span(location=date.timestamp() * 1000, 
                         dimension="height", 
                         line_color="grey", 
                         line_width=1.5, 
                         line_dash="dashed")
            
            p2.add_layout(vline)
            
            label = Label(
                x=date.timestamp() * 1000 + label_offset,  # Adjust to the right
                y=0.7,  # Example y position, adjust as needed
                text=label_text,
                text_color="grey",
                text_font_size="7pt"
            )
            p2.add_layout(label)

    # Use Div for title and subtitle
    title_div = Div(
        text=f"<h2>{title}</h2>", 
        styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"}
    )
    subtitle_div = Div(
        text=f"<p><em>{subtitle}</em></p>" if subtitle else "",
        styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"}
    )
    source_div = Div(
        text=f"<p><small>{source}</small></p>",
        styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"}
    )

    # Add limitations note if provided
    note_div = None
    if limitations_note:
        note_div = Div(
            text=f"""
            <div style="
                background-color: #f9f9f9; 
                border: 1px solid #dddddd; 
                padding: 10px; 
                border-radius: 5px;
                font-size: 12pt;
                margin-top: 10px;
                max-width: 800px;  /* Limit the width of the note */
                word-wrap: break-word;  /* Ensure text wraps within the width */
            ">
                <strong>Note:</strong> {limitations_note}
            </div>
            """,
        )

    # Combine all elements
    layout_elements = [title_div, subtitle_div, p2, source_div]
    if note_div:
        layout_elements.append(note_div)

    layout = column(*layout_elements)

    return layout


### Visualizing Business Activity Data by Vertical 

In [11]:
from bokeh.models import Div, Panel, Tabs
from bokeh.plotting import output_notebook, show
from bokeh.layouts import column

# Activate notebook output
output_notebook()

df_flood = (
    businessActivity2024_flood.groupby(["country", "business_vertical", "ds"])
    .mean("activity_quantile")[["activity_quantile"]]
    .reset_index()
)

df_cyclone = (
    businessActivity2024_extra.groupby(["country", "business_vertical", "ds"])
    .mean("activity_quantile")[["activity_quantile"]]
    .reset_index()
)


# Create a how to read it tab
def get_explanation_tab():
    """Create a tab explaining how to read the chart."""
    title_div = Div(
        text="<h2>How to read it?</h2>",
        styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"}
    )
    
    explanation_div = Div(
        text="""
        <p>This chart visualizes <strong>Business Activity Trends</strong> during the Bangladesh crisis compared to a 45-day pre-crisis baseline. 
        The metric used is the <em>Activity Quantile</em>, which compares daily activity levels to the baseline period.</p>
        <p><strong>Key Interpretation:</strong></p>
        <ul>
          <li>A value of <strong>0.5</strong> represents <em>normal</em> or <em>baseline-like</em> activity levels, typical of the pre-crisis period.</li>
          <li>Values <strong>above 0.5</strong> indicate increased business activity, showing a higher level of posts compared to the baseline.</li>
          <li>Values <strong>below 0.5</strong> indicate decreased business activity, suggesting lower activity levels relative to the baseline.</li>
        </ul>
        <p>The horizontal dashed line at <strong>0.5</strong> serves as a reference point for normal activity. Any significant deviation from this line highlights anomalous trends in business activity.</p>
        <p>Each colored line represents a different business vertical, allowing a comparative view of sectoral impacts during the crisis.</p>
        <hr>
        <p><strong>Limitations:</strong></p>
        <p>This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. 
        The methodology assumes that businesses post more frequently on Facebook when they are open and less frequently when they are closed. While this allows for insights into disruptions and recovery patterns, these assumptions may not hold true in all contexts. 
        For example, if businesses are posting about the ongoing crisis rather than regular operations, this could be interpreted as increased activity, potentially leading to misleading conclusions about their operational status.</p>
        """,
        styles={"text-align": "left", "font-size": "12pt"}
    )
    
    layout = column(title_div, explanation_div)
    return layout


# Create the tabs
tabs = []

# Tab 1: Cyclone Remal
tabs.append(
    TabPanel(
        child=get_line_plot(
            df_cyclone, 
            "Business Activity (May 27 2024 - 10 Jun 2024)",
            "Source: Data for Good, Meta",
            subtitle="National average during the Cyclone Remal compared to 45 days prior baseline (April 12th, 2024)", 
            limitations_note="This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. The methodology assumes businesses post more when open, which may not always be accurate."
        ),
        title="Cyclone Remal-Triggered",
    )
)

# Tab 2: Flood Crisis
tabs.append(
    TabPanel(
        child=get_line_plot(
            df_flood, 
            "Business Activity (Aug 25 2024 - Sep 5 2024)",
            "Source: Data for Good, Meta",
            subtitle="National average during the Bangladesh flood compared to 45 days prior baseline (July 11th, 2024)",
            vertical_dates=[datetime(2024, 8, 25), datetime(2024, 8, 29)],  # Example dates for vertical lines
            vertical_labels=["Rains from 08/21", "End of Flood"],  # Labels for the lines
            label_offset=0,  # Adjusts label position to the right
            limitations_note="This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. The methodology assumes businesses post more when open, which may not always be accurate."
        ),
        title="Flood-Triggered",
    )
)

# Add the explanation tab
tabs.append(
    TabPanel(
        child=get_explanation_tab(),
        title="How to read it?",
    )
)

# Display the tabs
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)


Loading BokehJS ...

In [12]:
import unicodedata

# Rename columns from shapefile to match activity data
bgd_adm2 = bgd_adm2.rename(columns={"ADM2_EN": "polygon_name"})
bgd_adm2["polygon_name"] = bgd_adm2["polygon_name"].str.upper()

# Rename columns from flood data to match activity data
remal_flood = remal_flood.rename(columns={"Admin2": "polygon_name"})
remal_flood["polygon_name"] = remal_flood["polygon_name"].str.upper()

august_flood = august_flood.rename(columns={"Admin2": "polygon_name"})
august_flood["polygon_name"] = august_flood["polygon_name"].str.upper()



### Analyzing Changes in Business Activity by Region 

In [13]:
# Add a temporary key  datasets
bgd_adm2["key"] = 1  # Adding a key for Cartesian join
businessActivity2024_flood["key"] = 1
businessActivity2024_extra["key"] = 1

# flood crisis
# Perform Cartesian join

businessActivity2024_flood['polygon_name'] = businessActivity2024_flood['polygon_name'].str.upper()

bgd_adm2_repeated_flood = pd.merge(
    bgd_adm2.drop(columns=["geometry"]),  # Drop geometry temporarily for the join
    businessActivity2024_flood,
    on=["key", "polygon_name"],  # Use the shared key for Cartesian product
    how="inner"
)

# Restore geometry column
bgd_adm2_repeated_flood = pd.merge(
    bgd_adm2_repeated_flood,
    bgd_adm2[["polygon_name", "geometry"]],
    on="polygon_name",
    how="left"
)

# Convert back to GeoDataFrame
bgd_adm2_merged_flood = gpd.GeoDataFrame(bgd_adm2_repeated_flood, geometry="geometry", crs=bgd_adm2.crs)

# Strip spaces from column names in august_flood
august_flood.columns = august_flood.columns.str.strip()

# add  polygon_name	Admin1	Observed_Area_SqKM	Flooded_Area_SqKM	Population_Exposed	Flooded Crop Area	Start_Date	End_Date	Flood_Percentage from  august_flood to bgd_adm2_merged_extra by polygon_name

bgd_adm2_merged_flood = pd.merge(
    bgd_adm2_merged_flood,
    august_flood[["polygon_name", "Observed_Area_SqKM", "Flooded_Area_SqKM", "Population_Exposed", "Flooded Crop Area", "Start_Date", "End_Date", "Flood_Percentage"]],
    on="polygon_name",
    how="left"
)

# cyclone crisis
# Perform Cartesian join

businessActivity2024_extra['polygon_name'] = businessActivity2024_extra['polygon_name'].str.upper()

bgd_adm2_repeated_extra = pd.merge(
    bgd_adm2.drop(columns=["geometry"]),  # Drop geometry temporarily for the join
    businessActivity2024_extra,
    on=["key", "polygon_name"],  # Use the shared key for Cartesian product
    how="inner"
)

# Restore geometry column
bgd_adm2_repeated_extra = pd.merge(
    bgd_adm2_repeated_extra,
    bgd_adm2[["polygon_name", "geometry"]],
    on="polygon_name",
    how="left"
)

# Convert back to GeoDataFrame
bgd_adm2_merged_extra = gpd.GeoDataFrame(bgd_adm2_repeated_extra, geometry="geometry", crs=bgd_adm2.crs)

# Strip spaces from column names in remal_flood
remal_flood.columns = remal_flood.columns.str.strip()

# add  polygon_name	Admin1	Observed_Area_SqKM	Flooded_Area_SqKM	Population_Exposed	Flooded Crop Area	Start_Date	End_Date	Flood_Percentage from  remal_flood to bgd_adm2_merged_extra by polygon_name

bgd_adm2_merged_extra = pd.merge(
    bgd_adm2_merged_extra,
    remal_flood[["polygon_name", "Observed_Area_SqKM", "Flooded_Area_SqKM", "Population_Exposed", "Flooded Crop Area", "Start_Date", "End_Date", "Flood_Percentage"]],
    on="polygon_name",
    how="left"
)

In [14]:
# Function to generate map plot
def map_plot(data, date=None, column_name="activity_quantile", title=None, source=None, subtitle=None):
    """
    Generate a static map plot encoded as a base64 image.
    If date is None, the function assumes a single map (e.g., flood percentage).
    """
    # Filter data (if a date is specified)
    if date:
        data_for_date = data[data["ds"] == date]
    else:
        data_for_date = data  # Use full dataset for flood percentage

    # Define colormap and normalization based on the data type
    cmap = cm.RdYlGn if column_name == "activity_quantile" else cm.Reds
    norm = TwoSlopeNorm(vmin=0, vcenter=0.5, vmax=1) if column_name == "activity_quantile" else Normalize(vmin=0, vmax=data_for_date[column_name].max())

    # Create the figure and axis
    fig, ax = plt.subplots(figsize=(7, 3))

    # Plot boundaries and the data
    data_for_date.boundary.plot(ax=ax, linewidth=0.5, color="white")  # Plot boundaries
    data_for_date.plot(
        column=column_name,
        cmap=cmap,
        norm=norm,
        linewidth=0.8,
        ax=ax,
        edgecolor="white",
        legend=True,
        legend_kwds={"label": column_name.replace("_", " ").title(), "orientation": "vertical"},
    )

    # Add title, subtitle, and source if provided
    if title:
        ax.set_title(title, fontsize=14, fontweight="bold")
    if subtitle:
        fig.text(0.5, 0.93, subtitle, ha='center', fontsize=12, style='italic')
    if source:
        fig.text(0.5, 0.01, source, ha='center', fontsize=10, style='italic')

    # Customize the plot
    ax.axis("off")  # Turn off axis

    # Save the plot to a BytesIO object
    buf = BytesIO()
    plt.savefig(buf, format="png", bbox_inches="tight")
    plt.close(fig)
    buf.seek(0)

    # Encode the image to base64
    img_base64 = base64.b64encode(buf.read()).decode("utf-8")
    buf.close()

    return img_base64

#### Cyclone Remal Business Activity Trends Dataset

This map visualizes **business activity trends** following **Cyclone Remal**, providing insights into economic disruptions and recovery in affected areas.

**Key Insights from Cyclone Remal (May-June 2024)**

Cyclone Remal caused severe **infrastructure damage, power outages, and business closures** across Bangladesh, particularly in coastal and urban areas. 

**Key Dates:**
- **May 26, 2024**: [Cyclone Remal made landfall near the Mongla and Khepupara coasts in Bangladesh and West Bengal, India.](https://www.ifrc.org/emergency/bangladesh-cyclone-remal)
- **May 27, 2024**: [Major highways and ports were disrupted, including Chattogram Port.](https://www.reuters.com/world/asia-pacific/millions-without-power-cyclone-remal-pounds-bangladesh-india-2024-05-27/)

**Key Places:**
- **Coastal districts (Bhola, Patuakhali, Barishal, Barguna, Pirojpur, Bagerhat, Khulna, and Satkhira)**: Severe **flooding and business shutdowns**.  
- **Urban centers (Dhaka, Chattogram, Khulna)**: **Transport and retail disruptions**, supply chain delays.  
- **Port cities (Chattogram, Mongla)**: **Cargo delays and trade slowdowns**.  


See more information in [Cyclone Remal: HCTT Humanitarian Response Plan 2024](https://bangladesh.un.org/sites/default/files/2024-06/BGD-TCRemal-HRP-FINAL%209June2024_0.pdf)


In [17]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64
from bokeh.io import show
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook

# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> during the Bangladesh crisis compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The first two tabs show the percentage of the area and population affected by the flood by admin region 2.</li>
          <li>The rest of the tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
          <li>Flood Percentage indicates how much of the region was affected by flooding.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-05-27", "2024-05-29", "2024-06-02", "2024-06-10"]
data_source = bgd_adm2_merged_extra  # Replace with actual data source

# Ensure Flood_Percentage column is of type float
# Ensure both Flood_Percentage and Population_Exposed are numeric
data_source["Flood_Percentage"] = pd.to_numeric(data_source["Flood_Percentage"], errors="coerce")
data_source["Population_Exposed"] = pd.to_numeric(data_source["Population_Exposed"].astype(str).str.replace(",", ""), errors="coerce")


# Create tabs list
tabs = []

# Add the Flood Percentage map as the first tab (only one)
tabs.append(
    TabPanel(
        child=get_map_tab(
            data_source,
            title="Flood Area",
            source="Source: United Nations Satellite Centre (UNOSAT)",
            subtitle="Percentage of the area affected by the flood by district, date considered: 2024-05-24 to 2024-05-29",
            column_name="Flood_Percentage"
        ),
        title="Flood Percentage"
    )
)

tabs.append(
    TabPanel(
        child=get_map_tab(
            data_source,
            title="Exposed Population",
            source="Source: United Nations Satellite Centre (UNOSAT)",
            subtitle="Population exposed by the flood by district, date considered: 2024-05-24 to 2024-05-29",
            column_name="Population_Exposed"
        ),
        title="Exposed Population"
    )
)

# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline during the Bangladesh Crisis"
            ),
            title=f"Activity Quantile ({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)



Loading BokehJS ...

#### Flood-Triggered Business Activity Trends Dataset

This map visualizes **business activity trends** during the flood period, allowing insights into mobility and recovery in these affected areas.

**Key Insights from the August 2024 Southeastern Floods in Bangladesh**

The August 2024 floods affected **73 upazilas** across **11 districts** in **northeastern** and **southeastern Bangladesh**, causing widespread disruptions. Below are the key insights:

**Key Dates:**
- **21 August**: Heavy rainfall from cloudbursts inundated eastern regions, including Feni, Cumilla, and Chattogram.
- **25 August**: Severe flooding reported in Noakhali and Lakshmipur.
- **26 August**: Release of water from India's Farakka Barrage intensified the flood situation.
- **27-29 August**: Floodwaters began receding, though high levels persisted in Monohorganj and parts of Noakhali.

**Key Places:**
- Severely affected districts: **Feni, Cumilla, Chattogram, Khagrachari, Noakhali, Moulvibazar, Habiganj, Brahmanbaria, Sylhet, Lakshmipur, and Cox's Bazar**.

More information in [Situation Report-3, Southeastern Flood in Bangladesh](https://bdrcs.org/wp-content/uploads/2024/08/BDRCS-Sitrep-3-Southeastern-Flood-August-2024.pdf).

In [16]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64
from bokeh.io import show
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook

# Activate notebook output
output_notebook()
# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)
    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})
    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)
    layout = column(title_div, subtitle_div, img_div, source_div)
    return layout
# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> during the Bangladesh crisis compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The first two tabs show the percentage of the area and population affected by the flood by admin region 2.</li>
          <li>The rest of the tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
          <li>Flood Percentage indicates how much of the region was affected by flooding.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})
    
    return column(title_div, explanation_div)
# Define selected dates for business activity

selected_dates = ["2024-08-25", "2024-08-27","2024-08-29", "2024-09-05"]
data_source = bgd_adm2_merged_flood 


# Ensure both Flood_Percentage and Population_Exposed are numeric
data_source["Flood_Percentage"] = pd.to_numeric(data_source["Flood_Percentage"], errors="coerce")
data_source["Population_Exposed"] = pd.to_numeric(data_source["Population_Exposed"].astype(str).str.replace(",", ""), errors="coerce")

# Create tabs list
tabs = []
# Add the Flood Percentage map as the first tab (only one)
tabs.append(
    TabPanel(
        child=get_map_tab(
            data_source,
            title="Flood Area",
            source="Source: United Nations Satellite Centre (UNOSAT)",
            subtitle="Percentage of the area affected by the flood by district, date considered: 2024-08-21 to 2024-08-29",
            column_name="Flood_Percentage"
        ),
        title="Flood Percentage"
    )
)
tabs.append(
    TabPanel(
        child=get_map_tab(
            data_source,
            title="Exposed Population",
            source="Source: United Nations Satellite Centre (UNOSAT)",
            subtitle="Population exposed by the flood by district, date considered: 2024-08-21 to 2024-08-29",
            column_name="Population_Exposed"
        ),
        title="Exposed Population"
    )
)
# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline during the Bangladesh Crisis"
            ),
            title=f"Activity Quantile ({date})"
        )
    )
# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))
# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...